
File: 07-lecture_solution.py


Michel Bierlaire

Thu Aug 22 15:49:35 2024




In [ ]:

from IPython.core.display_functions import display
import biogeme.biogeme_logging as blog
from biogeme.biogeme import BIOGEME
from biogeme.expressions import Beta, log
from biogeme.models import loglogit, logit
from biogeme.results import bioResults, compile_estimation_results


Variables used for the specification of the Swissmetro model are defined in the file `swissmetro_variables.py`.

In [ ]:
from swissmetro_variables import (
    database,
    CHOICE,
    TRAIN_AV_SP,
    SM_AV,
    CAR_AV_SP,
    TRAIN_TT_SCALED,
    TRAIN_COST_SCALED,
    TRAIN_HE_SCALED,
    SM_TT_SCALED,
    SM_COST_SCALED,
    SM_HE_SCALED,
    CAR_TT_SCALED,
    CAR_CO_SCALED,
)


As the estimation time may be long, we ask Biogeme to report the details of the iterations.

In [ ]:
logger = blog.get_screen_logger(level=blog.INFO)


# Parameters

In [ ]:
asc_car = Beta('asc_car', 0, None, None, 0)
asc_train = Beta('asc_train', 0, None, None, 0)
b_time = Beta('b_time', 0, None, None, 0)
b_cost = Beta('b_cost', 0, None, None, 0)
b_fr = Beta('b_fr', 0, None, None, 0)



# Availability conditions

In [ ]:
av = {1: TRAIN_AV_SP, 2: SM_AV, 3: CAR_AV_SP}



# Logit model

## Utility functions

In [ ]:
V1 = (
    asc_train
    + b_time * TRAIN_TT_SCALED
    + b_cost * TRAIN_COST_SCALED
    + b_fr * TRAIN_HE_SCALED
)
V2 = b_time * SM_TT_SCALED + b_cost * SM_COST_SCALED + b_fr * SM_HE_SCALED
V3 = asc_car + b_time * CAR_TT_SCALED + b_cost * CAR_CO_SCALED
V = {1: V1, 2: V2, 3: V3}



## Model

In [ ]:
logprob = loglogit(V, av, CHOICE)



## Estimation

In [ ]:
biogeme = BIOGEME(database, logprob)
biogeme.modelName = '01logit'
results_logit: bioResults = biogeme.estimate(recycle=True)



## Results

General statistics

In [ ]:
print(results_logit.print_general_statistics())


Estimated parameters

In [ ]:
param_logit = results_logit.get_estimated_parameters()
display(param_logit)



# Random parameter: normal distribution

Read the results from file

In [ ]:
results_normal = bioResults(pickle_file='02normal.pickle')



# Random parameter: lognormal distribution

Read the results from file

In [ ]:
results_lognormal = bioResults(pickle_file='03lognormal.pickle')



# Latent classes

We consider two classes in the population. The first class of individuals have considered all variables when making
their choice. For them, the specification of the utility function is the same as for the logit model.

In [ ]:
V1_class_1 = (
    asc_train
    + b_time * TRAIN_TT_SCALED
    + b_cost * TRAIN_COST_SCALED
    + b_fr * TRAIN_HE_SCALED
)
V2_class_1 = b_time * SM_TT_SCALED + b_cost * SM_COST_SCALED + b_fr * SM_HE_SCALED
V3_class_1 = asc_car + b_time * CAR_TT_SCALED + b_cost * CAR_CO_SCALED
V_class_1 = {1: V1_class_1, 2: V2_class_1, 3: V3_class_1}



The second class of individuals ignored the travel time variable when making the choice. Therefore, this variable
is removed from the utility function.

In [ ]:
V1_class_2 = asc_train + b_cost * TRAIN_COST_SCALED + b_fr * TRAIN_HE_SCALED
V2_class_2 = b_cost * SM_COST_SCALED + b_fr * SM_HE_SCALED
V3_class_2 = asc_car + b_cost * CAR_CO_SCALED
V_class_2 = {1: V1_class_2, 2: V2_class_2, 3: V3_class_2}



The following parameter captures the probability to belong to class 1.

In [ ]:
omega = Beta('omega', 0.5, 0, 1, 0)
prob_class_1 = omega
prob_class_2 = 1 - omega



## Model

We first calculate the choice probability for each class.

In [ ]:
choice_prob_class_1 = logit(V_class_1, av, CHOICE)
choice_prob_class_2 = logit(V_class_2, av, CHOICE)



The choice probability is obtained by using the class membership model.

In [ ]:
choice_prob = prob_class_1 * choice_prob_class_1 + prob_class_2 * choice_prob_class_2
logprob = log(choice_prob)



## Estimation

In [ ]:
biogeme = BIOGEME(database, logprob)
biogeme.modelName = '04latentClass'
results_latent = biogeme.estimate()



## Results

General statistics

In [ ]:

print(results_latent.print_general_statistics())


Estimated parameters

In [ ]:

param_latent = results_latent.get_estimated_parameters()
display(param_latent)



# Comparison

We build a summary data frame.

In [ ]:

summary = compile_estimation_results(
    {
        'Logit': results_logit,
        'Random param. (normal)': results_normal,
        'Random param. (lognormal)': results_lognormal,
        'Latent class': results_latent,
    }
)
display(summary[0])


We note that the probability to belong to class one is...

In [ ]:
estimated_proba_class_1 = param_latent.at['omega', 'Value']
print(f'Probability to belong to class 1: {100 * estimated_proba_class_1:.3g}%.')